In [2]:
import pvlib
from pvlib.pvsystem import PVSystem

from pvlib.location import Location

from pvlib.modelchain import ModelChain
from pvlib.temperature import TEMPERATURE_MODEL_PARAMETERS
import matplotlib.pyplot as plt 
import pandas as pd
import datetime
import math
import numpy as np
from math import sqrt
import scipy.interpolate
import pandas as pd
import plotly.express as px

In [199]:
df_meta = pd.read_csv("../../Data/System/PV system information dataset TU WIEN.csv", sep = ";", index_col=0)
df_meta = df_meta.iloc[:,1:]
df_meta["tilt"] = df_meta["tilt"].str.replace(",",".")
df_meta["azimuth"] = df_meta["azimuth"].str.replace(",",".")
df_meta = df_meta.astype("float")
total_cap = df_meta["estimated capacity"].sum() / 10**6

In [6]:
df_power = pd.read_csv("../../Input_Data/PV_System_Power.csv", index_col=0, parse_dates=True)


In [7]:

df_power.columns = [int(col) for col in df_power.columns]

target_timesteplen = "1H"


In [144]:
df_irr = pd.read_csv("../../Data/Meteo/GHI_DNI_DHI.csv", index_col=0, parse_dates=True)
df_irr = df_irr.iloc[:,2:]
print(df_irr.columns)
df_irr.columns = ["dhi", "dni", "ghi"]
df_irr = df_irr.resample(target_timesteplen).mean()
df_irr = df_irr.tz_localize(None)
first_timestep = df_irr.index[0]
last_timestep = df_irr.index[-1]


Index(['Dhi', 'Dni', 'Ghi'], dtype='object')


In [132]:
d

dhi  dni  ghi
PeriodEnd                         
2015-01-01 00:00:00  0.0  0.0  0.0
2015-01-01 01:00:00  0.0  0.0  0.0
2015-01-01 02:00:00  0.0  0.0  0.0
2015-01-01 03:00:00  0.0  0.0  0.0
2015-01-01 04:00:00  0.0  0.0  0.0
...                  ...  ...  ...
2016-01-01 19:00:00  0.0  0.0  0.0
2016-01-01 20:00:00  0.0  0.0  0.0
2016-01-01 21:00:00  0.0  0.0  0.0
2016-01-01 22:00:00  0.0  0.0  0.0
2016-01-01 23:00:00  0.0  0.0  0.0

[8784 rows x 3 columns]

In [145]:

system_id = 281
df = df_power[[system_id]]
df = df.resample(target_timesteplen).mean()

df = df[first_timestep:last_timestep]

In [146]:
df

281
DateTime                
2015-01-01 00:00:00  0.0
2015-01-01 01:00:00  0.0
2015-01-01 02:00:00  0.0
2015-01-01 03:00:00  0.0
2015-01-01 04:00:00  0.0
...                  ...
2016-01-01 19:00:00  NaN
2016-01-01 20:00:00  NaN
2016-01-01 21:00:00  NaN
2016-01-01 22:00:00  NaN
2016-01-01 23:00:00  NaN

[8784 rows x 1 columns]

# My Method

In [11]:
from sklearn.metrics import mean_squared_error
from sklearn.preprocessing import MinMaxScaler

def infer_tilt_azimuth(df_irr, combinations, row, df_measurements):

    "Pass a dataset for PV Meta Data: Location, Tilt, Azimuth, Capacity and a Dataset for irradiance: DNI, DHI, GHI to calculate profiles with PV Watts"
    
    start_1 = pd.Timestamp("20150501")
    end_1 = pd.Timestamp("20150513")

    start_2 = pd.Timestamp("20160606")
    end_2 = pd.Timestamp("20160610")

    latitude, longitude, tilt_estimated, azimuth_estimated, capacity = row

    first_timestep = df_measurements.index[0]
    last_timestep = df_measurements.index[-1]
    df_irr = df_irr[first_timestep:last_timestep]
    n_combis = len(combinations)
    counter = 0
    errors = {}
    for combi in combinations:
        counter += 1
        tilt = combi[0]
        azimuth = combi[1]
        
        temperature_model_parameters = TEMPERATURE_MODEL_PARAMETERS['sapm']['open_rack_glass_glass']

        location = Location(latitude=latitude, longitude=longitude)

        pvwatts_system = PVSystem(surface_tilt= tilt , surface_azimuth=azimuth,
            module_parameters={'pdc0': capacity, 'gamma_pdc': -0.004},
            inverter_parameters={'pdc0': capacity},
            temperature_model_parameters=temperature_model_parameters)
        
        mc = ModelChain(pvwatts_system, location, aoi_model='physical', spectral_model='no_loss')
        mc.run_model(df_irr)
        results = mc.results.ac
        df_results = pd.Series(results)
        df_results.index = df_results.index.tz_localize(None)
        df_results.index.name = "timestamp"

        df_compare = pd.merge(df_results,df_measurements, left_index=True, right_index=True)

        scaler = MinMaxScaler()
        df_compare[df_compare.columns] = scaler.fit_transform(df_compare[df_compare.columns])
        
        
        df_compare = df_compare.replace(0,np.nan) #excluding the 0s in the error calculations
        df_compare.dropna(inplace=True)

        if counter % int((0.05*n_combis)) == 0: #plot every 5% of iterations
            print(counter)
            print(df_compare.head())
        errors[combi] = mean_squared_error(df_compare.iloc[:,:1], df_compare.iloc[:,-1:])
    
    #picking out the tilt/azimuth combination with the lowest error
    df_errors = pd.DataFrame.from_dict(errors, orient = "index")
    df_errors.sort_values(by = 0)

    print(df_errors.head(20))

    tilt_derived = df_errors.iloc[:1,:].index[0][0]
    azimuth_derived = df_errors.iloc[:1,:].index[0][1]

    print("Old Azimuth was {0} and new azimuth is {1}".format(azimuth_estimated, azimuth_derived))
    print("Old Tilt was {0} and new tilt is {1}".format(tilt_estimated, tilt_derived))

    return tilt_derived, azimuth_derived

In [34]:

def physical_profile(row):
    latitude, longitude, tilt, azimuth, capacity = row

    temperature_model_parameters = TEMPERATURE_MODEL_PARAMETERS['sapm']['open_rack_glass_glass']

    location = Location(latitude=latitude, longitude=longitude)

    pvwatts_system = PVSystem(surface_tilt= tilt , surface_azimuth=azimuth,
        module_parameters={'pdc0': capacity, 'gamma_pdc': -0.004},
        inverter_parameters={'pdc0': capacity},
        temperature_model_parameters=temperature_model_parameters)
    
    mc = ModelChain(pvwatts_system, location, aoi_model='physical', spectral_model='no_loss')
    mc.run_model(df_irr)
    results = mc.results.ac

    df_results = pd.Series(results)
    df_results.index = df_results.index.tz_localize(None)
    df_results.index.name = "timestamp"
    df_results.name =  str(tilt)+ ";" +str(azimuth)

    return df_results

In [98]:
df_meta = df_meta.loc[df_power.columns]

row = df_meta.loc[system_id]

In [86]:
df = df_power[[system_id]]

df = df.resample(target_timesteplen).mean()


In [88]:
np.random.seed()

In [172]:
import itertools
tilt_azimuth_combinations = list(itertools.product(range(0,91,3), range(0,361,10)))

In [186]:
def meta_data_iteration(measurements, row, tilt_azimuth_combinations):
    errors = {}
    counter = 0
    n_combis = len(tilt_azimuth_combinations)
    for tilt, azi in tilt_azimuth_combinations:
        key = str(tilt)+";"+str(azi)
        row[2] = tilt
        row[3] = azi
        df_phys = physical_profile(row)

        df_merged = pd.merge(df_phys, measurements, left_index=True, right_index=True)
        df_merged = df_merged.replace(0,np.nan).dropna()
        
        error = mean_absolute_error(df_merged.iloc[:,:1], df_merged.iloc[:,1:])
        errors[key] = error
        
        counter +=1
        if counter % int((0.1*n_combis)) == 0: #plot every 5% of iterations
            print("Calculation is {0}% complete".format((counter/n_combis)*100))
            timeseries_plotter(df_merged, 1)
    return errors
    

In [182]:
from sklearn.metrics import mean_absolute_error
from timeseries_functions import timeseries_plotter

In [183]:
def tilt_azimuth_getter(mae):
    df_errors = pd.Series(mae)
    argmin_index = df_errors.argmin()
    tilt, azimuth = df_errors.index[argmin_index].split(";")
    return int(tilt), int(azimuth)

In [184]:
def tilt_azimuth_inference(measurements,row, tilt_azimuth_combinations):
    errors = meta_data_iteration(measurements, row, tilt_azimuth_combinations)
    tilt, azimuth = tilt_azimuth_getter(errors)
    return tilt, azimuth

    

In [ ]:
optimal_tilt_azimuth = {}

for system_id in df_power.columns:
    print("Starting System_ID:{}".format(system_id))
    df = df_power[system_id]
    row = df_meta.loc[system_id]
    tilt, azimuth = tilt_azimuth_inference(df, row, tilt_azimuth_combinations)
    optimal_tilt_azimuth[system_id] = (tilt, azimuth)

    print("--------")


In [252]:
df_meta_derived = pd.DataFrame.from_dict(optimal_tilt_azimuth, "index", columns = ["tilt_derived", "azimuth_derived"])

In [253]:
df_meta_original = df_meta

df_meta_ad = pd.merge(df_meta_original,df_meta_derived, left_index=True, right_index=True)
df_meta_ad["tilt_drift"] = abs(df_meta_ad["tilt"] - df_meta_ad["tilt_derived"])
df_meta_ad["azimuth_drift"] = abs(df_meta_ad["azimuth"] - df_meta_ad["azimuth_derived"])

In [264]:
def tilt_azimuth_combinations_creator(row):

    tilt = int(row["tilt_derived"])
    azimuth = int(row["azimuth_derived"])
    tilt_tol = int(row["tilt_drift"])
    azimuth_tol = int(row["azimuth_drift"])

    tilt_lower = max(0,tilt-tilt_tol)
    #print(tilt_lower)
    tilt_upper = min(90, tilt+tilt_tol)
    #print(tilt_upper)
    azimuth_lower = max(0, azimuth-azimuth_tol)
    #print(azimuth_lower)
    azimuth_upper = min(360,azimuth+azimuth_tol)
    #print(azimuth_upper)
    
    tilt_azimuth_combinations = list(itertools.product(range(tilt_lower,tilt_upper,1), range(azimuth_lower,azimuth_upper,1)))

    row["tilt"] = tilt
    row["azimuth"] = azimuth
    row = row[:5]

    return row, tilt_azimuth_combinations


In [265]:
def meta_data_iteration_finetune(measurements, row):

    row, tilt_azimuth_combinations = tilt_azimuth_combinations_creator(row)
    errors = {}
    counter = 0
    n_combis = len(tilt_azimuth_combinations)
    for tilt, azi in tilt_azimuth_combinations:
        key = str(tilt)+";"+str(azi)
        row[2] = tilt
        row[3] = azi
        df_phys = physical_profile(row)

        df_merged = pd.merge(df_phys, measurements, left_index=True, right_index=True)
        df_merged = df_merged.replace(0,np.nan).dropna()
        
        error = mean_absolute_error(df_merged.iloc[:,:1], df_merged.iloc[:,1:])
        errors[key] = error
        
        counter +=1
        if counter % int((0.1*n_combis)) == 0: #plot every 5% of iterations
            print("Calculation is {0}% complete".format((counter/n_combis)*100))
            #timeseries_plotter(df_merged, 1)
    return errors

In [266]:
def tilt_azimuth_inference_finetune(measurements,row):
    errors = meta_data_iteration_finetune(measurements, row)
    tilt, azimuth = tilt_azimuth_getter(errors)
    return tilt, azimuth

In [ ]:
optimal_tilt_azimuth_finetune = {}

for system_id in df_power.columns:
    print("Starting System_ID:{}".format(system_id))
    df = df_power[system_id]
    row = df_meta_ad.loc[system_id]
    tilt, azimuth = tilt_azimuth_inference_finetune(df, row)
    optimal_tilt_azimuth_finetune[system_id] = (tilt, azimuth)

    print("--------")

In [271]:
df_meta_derived_finetuned = pd.DataFrame.from_dict(optimal_tilt_azimuth, "index", columns = ["tilt_finetuned", "azimuth_finetuned"])

In [274]:
df_new_meta = pd.concat([df_meta_derived, df_meta_derived_finetuned], axis = 1)

In [277]:
os.getcwd()

'/Users/nikolaushouben/Library/Mobile Documents/com~apple~CloudDocs/PhD_Icloud/PhD_Research/Paper_2_Collaborative Forecasting/Code/Collaborative_PV_Forecasting'

In [278]:
df_new_meta.iloc[:,-2:].to_csv("../../Input_Data/Meta_Data_PV_Optimised.csv")

In [171]:
fig = px.line(df_compare)
fig.update_xaxes(rangeslider_visible=True)
fig.show()